In [2]:
import os
import sys
!pip install matplotlib==3.7.0
import pandas as pd
from tqdm import tqdm
import sentence_transformers
import transformers
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
os.chdir("../../../../../../..")
os.chdir("home/user/mnt/degelin/thesis")
import torch
from torch.amp import autocast
import numpy as np
print("PyTorch version:", torch.__version__)
print("CUDA available:", torch.cuda.is_available())
print("CUDA version:", torch.version.cuda)
print("Available devices:")
print(torch.cuda.device_count())
for i in range(torch.cuda.device_count()):
    print(f"  Device {i}: {torch.cuda.get_device_name(i)}")
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using device: {device}")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.6/11.6 MB 12.1 MB/s eta 0:00:0000:010:01
  Attempting uninstall: matplotlib
    Found existing installation: matplotlib 3.8.1
    Uninstalling matplotlib-3.8.1:
      Successfully uninstalled matplotlib-3.8.1
PyTorch version: 2.4.0+cu121
CUDA available: True
CUDA version: 12.1
Available devices:
1
  Device 0: NVIDIA RTX A6000
Using device: cuda


In [8]:
def create_save_path(model_name):
    if '/' in model_name:
        model_name_parts = model_name.split('/')
        model_name_save_path = '-'.join(model_name_parts)
    else:
        model_name_save_path = model_name
    return model_name_save_path
def encode_and_return(data, column_name, model, batch_size=64):
    total_items = len(data)
    embeddings = []

    with autocast("cuda"):
        for idx in range(0, total_items, batch_size):
            batch = data[column_name].iloc[idx:idx+batch_size].tolist()
            batch_embeddings = model.encode(batch, show_progress_bar=False, device="cuda")
            embeddings.extend(batch_embeddings)
    
    print('Embeddings generation done.')
    print(f'Total embeddings generated: {len(embeddings)}')
    return np.array(embeddings)

def load_embeddings(checkpoint_file):
    if os.path.exists(checkpoint_file):
        checkpoint = torch.load(checkpoint_file, weights_only=False)
        embeddings = np.array(checkpoint['embeddings'])
        return embeddings
    else:
        raise FileNotFoundError(f"Checkpoint file {checkpoint_file} does not exist.")

def get_grant_values(application_ids, full_data):
    grant_value_dict = dict(zip(full_data['APPLICATION_ID'], full_data['GRANT_VALUE']))
    grant_values = [grant_value_dict.get(app_id) for app_id in application_ids]
    return grant_values

def get_FOA_values(application_ids, full_data):
    grant_value_dict = dict(zip(full_data['APPLICATION_ID'], full_data['FOA_NUMBER']))
    foa_values = [grant_value_dict.get(app_id) for app_id in application_ids]
    return foa_values

def determine_output_file_path(model_path, rs_file_path):
    # Define the output paths
    if 'without' in rs_file_path.lower():
        output_path = 'good_code/output_csvs/without/'
    else:
        output_path = 'good_code/output_csvs/with/'
    
    # Extract tuned_data and tuned_model from model_path
    parts = model_path.split('fine_tuned_models/')[1].split('/')
    tuned_data = parts[0]
    tuned_model = '_'.join(parts[1:])  # Join remaining parts with '_'
    
    # Construct the final model_path
    final_model_path = os.path.join(output_path, tuned_data + tuned_model)
    
    return final_model_path
    
def get_top_5_closest(proj_emb, grant_embs, grant_ids):
    cos_similarities = cosine_similarity(proj_emb.reshape(1, -1), grant_embs)[0]
    top_indices = cos_similarities.argsort()[-5:][::-1]
    top_grant_ids = [grant_ids[idx] for idx in top_indices]
    return top_grant_ids

def process_model(model_path, rs_file_path):
    print('in process_model')
    output_file_path = determine_output_file_path(model_path,rs_file_path)
    model = SentenceTransformer(model_path)
    rs_file = pd.read_csv(rs_file_path)
    rs_file['PROJECT_DESCRIPTION'] = rs_file['PROJECT_DESCRIPTION'].astype(str)
    rs_file['GRANT_DESCRIPTION'] = rs_file['GRANT_DESCRIPTION'].astype(str)
    
    # Encode and save embeddings
    proj_embeddings = encode_and_return(rs_file, 'PROJECT_DESCRIPTION', model)
    grant_embeddings = encode_and_return(full_data_file, 'GRANT_DESCRIPTION', model)
    
    grant_ids = full_data_file['APPLICATION_ID'].astype(str).tolist()
    
    rs_file['APPLICATION_IDs'] = np.nan
    rs_file['REC_GRANT_VALUES'] = np.nan
    rs_file['REC_FOA_NUMBERS'] = np.nan

    num_projects = len(rs_file)
    print(num_projects)
    
    for idx in tqdm(range(num_projects), desc="Processing Projects", unit="project"):
        proj_emb = proj_embeddings[idx]
        
        top_grant_ids = get_top_5_closest(proj_emb, grant_embeddings, grant_ids)
        top_grant_values = get_grant_values(top_grant_ids, full_data_file)
        foas = get_FOA_values(top_grant_ids, full_data_file)
        
        top_grant_ids_str = [str(id) for id in top_grant_ids]
        top_grant_values_str = [str(value) for value in top_grant_values]
        foas_str = [str(id) for id in foas]
        
        rs_file.loc[idx, 'APPLICATION_IDs'] = ','.join(top_grant_ids_str)
        rs_file.loc[idx, 'REC_GRANT_VALUES'] = ','.join(top_grant_values_str)
        rs_file.loc[idx, 'REC_FOA_NUMBERS'] = ','.join(foas_str)
        
    columns_to_drop = ['GRANT_ID', 'label', 'PROJECT_DESCRIPTION', 'GRANT_DESCRIPTION']
    rs_file = rs_file.drop(columns=columns_to_drop)
    rs_file.to_csv(output_file_path, index=False)
    print("Processing completed and CSV saved.")

In [9]:
model_paths = ['good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-FacebookAI-roberta-base-2024-08-01_06-47-12', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-FacebookAI-xlm-roberta-base-2024-08-01_06-56-53', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-SpanBERT-spanbert-base-cased-2024-08-01_07-24-10', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-albert-albert-base-v2-2024-08-01_07-13-34', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-allenai-scibert_scivocab_uncased-2024-08-01_08-04-49', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-bionlp-bluebert_pubmed_mimic_uncased_L-12_H-768_A-12-2024-08-01_08-13-45', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-distilbert-distilbert-base-uncased-2024-08-01_07-07-48', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-dmis-lab-biobert-base-cased-v1.1-2024-08-01_07-56-00', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-bert-bert-base-multilingual-uncased-2024-08-01_06-29-01', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-bert-bert-base-uncased-2024-08-01_06-38-16', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-bert_uncased_L-12_H-768_A-12-2024-08-01_08-53-12', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-bert_uncased_L-2_H-128_A-2-2024-08-01_08-31-36', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-bert_uncased_L-2_H-256_A-4-2024-08-01_08-34-11', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-bert_uncased_L-4_H-256_A-4-2024-08-01_08-36-49', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-bert_uncased_L-4_H-512_A-8-2024-08-01_08-39-35', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-bert_uncased_L-6_H-512_A-8-2024-08-01_08-42-52', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-bert_uncased_L-8_H-768_A-12-2024-08-01_08-46-37', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-google-electra-base-discriminator-2024-08-01_07-46-26', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-microsoft-BiomedNLP-BiomedBERT-base-uncased-abstract-fulltext-2024-08-01_08-22-47', 'good_code/fine_tuned_models/perfect_withoutNames/fine_tuning-microsoft-deberta-base-2024-08-01_07-33-03', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-FacebookAI-roberta-base-2024-07-31_09-06-44', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-FacebookAI-xlm-roberta-base-2024-07-31_09-23-31', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-SpanBERT-spanbert-base-cased-2024-07-31_10-10-38', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-albert-albert-base-v2-2024-07-31_09-51-52', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-allenai-scibert_scivocab_uncased-2024-07-31_11-21-57', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-bionlp-bluebert_pubmed_mimic_uncased_L-12_H-768_A-12-2024-07-31_11-37-27', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-distilbert-distilbert-base-uncased-2024-07-31_09-41-43', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-dmis-lab-biobert-base-cased-v1.1-2024-07-31_11-06-28', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-google-bert-bert-base-multilingual-uncased-2024-07-31_08-35-34', 'good_code/fine_tuned_models/reality_withNames/fine_tuning-google-bert-bert-base-uncased-2024-07-31_08-51-18']

In [10]:
#model_path = 'good_code/fine_tuned_models/original_withNames/fine_tuning-albert-albert-base-v2-2024-08-01_02-43-08'
full_data_file = pd.read_csv('good_code/updated_projects_labelled_inflation_adjusted2_modified.csv')
data_files = ['good_code/RS_withoutNames.csv']

#process_model(model_path, 'good_code/RS_withNames.csv')

In [11]:
def process_all_models_and_files(model_paths, data_files):
    total_combinations = len(model_paths) * len(data_files)
    with tqdm(total=total_combinations, desc='Processing Models and Files') as pbar:
        for model_path in model_paths:
            for data_file in data_files:
                process_model(model_path, data_file)
                pbar.update(1)

In [ ]:
process_all_models_and_files(model_paths, data_files)

Processing Models and Files:   0%|                       | 0/30 [00:00<?, ?it/s]

in process_model
Embeddings generation done.
Total embeddings generated: 3706
Embeddings generation done.
Total embeddings generated: 80845
3706



Processing Projects:   0%|                        | 0/3706 [00:00<?, ?project/s]/tmp/ipykernel_5043/1369730561.py:95: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '9843530,10083763,9657194,10335171,9172674' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'APPLICATION_IDs'] = ','.join(top_grant_ids_str)
/tmp/ipykernel_5043/1369730561.py:96: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'REC_GRANT_VALUES'] = ','.join(top_grant_values_str)
/tmp/ipykernel_5043/1369730561.py:97: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, p

Processing completed and CSV saved.
in process_model
Embeddings generation done.
Total embeddings generated: 3706
Embeddings generation done.
Total embeddings generated: 80845
3706



Processing Projects:   0%|                        | 0/3706 [00:00<?, ?project/s]/tmp/ipykernel_5043/1369730561.py:95: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '10335171,9843530,9657194,10083763,10207226' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'APPLICATION_IDs'] = ','.join(top_grant_ids_str)
/tmp/ipykernel_5043/1369730561.py:96: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'REC_GRANT_VALUES'] = ','.join(top_grant_values_str)
/tmp/ipykernel_5043/1369730561.py:97: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, 

...


Processing Projects:   0%|                        | 0/3706 [00:00<?, ?project/s]/tmp/ipykernel_5043/1369730561.py:95: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '9319794,8997188,9144844,9145766,9323560' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'APPLICATION_IDs'] = ','.join(top_grant_ids_str)
/tmp/ipykernel_5043/1369730561.py:96: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'REC_GRANT_VALUES'] = ','.join(top_grant_values_str)
/tmp/ipykernel_5043/1369730561.py:97: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, ple

Processing completed and CSV saved.
in process_model
Embeddings generation done.
Total embeddings generated: 3706
Embeddings generation done.
Total embeddings generated: 80845
3706



Processing Projects:   0%|                        | 0/3706 [00:00<?, ?project/s]/tmp/ipykernel_5043/1369730561.py:95: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '9657194,10083763,9843530,10335171,8959886' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'APPLICATION_IDs'] = ','.join(top_grant_ids_str)
/tmp/ipykernel_5043/1369730561.py:96: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'REC_GRANT_VALUES'] = ','.join(top_grant_values_str)
/tmp/ipykernel_5043/1369730561.py:97: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, p

Processing completed and CSV saved.
in process_model
Embeddings generation done.
Total embeddings generated: 3706
Embeddings generation done.
Total embeddings generated: 80845
3706



Processing Projects:   0%|                        | 0/3706 [00:00<?, ?project/s]/tmp/ipykernel_5043/1369730561.py:95: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '8885344,8693006,8377254,8379824,8318831' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'APPLICATION_IDs'] = ','.join(top_grant_ids_str)
/tmp/ipykernel_5043/1369730561.py:96: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  rs_file.loc[idx, 'REC_GRANT_VALUES'] = ','.join(top_grant_values_str)
/tmp/ipykernel_5043/1369730561.py:97: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'None,None,None,None,None' has dtype incompatible with float64, ple